In [1]:
import numpy as np
import pandas as pd
import nltk
from nltk.corpus import gutenberg
from datetime import datetime

import re
import matplotlib.pyplot as plt

import unicodedata
from contractions import CONTRACTION_MAP

from nltk.stem import WordNetLemmatizer
from nltk.tokenize.toktok import ToktokTokenizer
import pdfplumber

from importlib import reload
#import numpy as np
#import pandas as pd
#import nltk
#from nltk.corpus import gutenberg
#from datetime import datetime

#import rehttp://localhost:8888/notebooks/Desktop/Escuela/procesamiento_textos/Text%20Similarity/Text_similarity_for_papers_v2.ipynb#

#import matplotlib.pyplot as plt

pd.options.display.max_colwidth = 200
%matplotlib inline

In [2]:
import utils as utils

In [3]:
# Leer csvy se pasa a DataFrame
df = pd.read_csv("dataset/archive/Train.csv")
df

id  \
0       1824   
1       3094   
2       8463   
3       2082   
4       8687   
...      ...   
13999   8699   
14000  11912   
14001   4842   
14002  12507   
14003   1724   

                                                                                                                                                                                                      ABSTRACT  \
0      a ever-growing datasets inside observational astronomy have challenged scientists inside many aspects, including an efficient and interactive data exploration and visualization. many tools have be...   
1      we propose the framework considering optimal $t$-matchings excluding a prescribed $t$-factors inside bipartite graphs. a proposed framework was the generalization of a nonbipartite matching proble...   
2      nanostructures with open shell transition metal or molecular constituents host often strong electronic correlations and are highly sensitive to atomistic material details. this tutorial review dis...   
3      stars are self-gravitating fluids inside which pressure, buoyancy, rotation and magnetic fields provide a restoring forces considering global modes of oscillation. pressure and buoyancy energetica...   
4      deep neural perception and control networks are likely to be the key component of self-driving vehicles. these models need to be explainable - they should provide easy-to-interpret rationales cons...   
...                                                                                                                                                                                                        ...   
13999  a methodology of automatic detection of a event basis of information operations, reflected inside thematic information flows, was described. a presented methodology was based on a technologies con...   
14000  we consider a case inside which the robot has to navigate inside an unknown environment but does not have enough on-board power or payload to carry the traditional depth sensor (e.g., the 3d lidar...   
14001  despite being usually considered two competing phenomena, charge-density-wave and superconductivity coexist inside few systems, a most emblematic one being a transition metal dichalcogenide 2h-nbs...   
14002  we present the framework and its implementation relying on natural language processing methods, which aims at a identification of exercise item candidates from corpora. a hybrid system combining h...   
14003  here we report small-angle neutron scattering (sans) measurements and theoretical modeling of u$_3$al$_2$ge$_3$. analysis of a sans data reveals the phase transition to sinusoidally modulated magn...   

       Computer Science  Mathematics  Physics  Statistics  Analysis of PDEs  \
0                     0            0        1           0                 0   
1                     1            0        0           0                 0   
2                     0            0        1           0                 0   
3                     0            0        1           0                 0   
4                     1            0        0           0                 0   
...                 ...          ...      ...         ...               ...   
13999                 1            0        0           0                 0   
14000                 1            0        0           0                 0   
14001                 0            0        1           0                 0   
14002                 1            0        0           0                 0   
14003                 0            0        1           0                 0   

       Applications  Artificial Intelligence  Astrophysics of Galaxies  ...  \
0                 0                        0                         0  ...   
1                 0                        0                         0  ...   
2                 0                        0                         0  ...   
3                 0            

In [6]:
# Obtención de los documentos, que en este caso son los resumenes en inglés de artículos científicos
corpus= df["ABSTRACT"]
corpus = corpus.to_numpy()
corpus

array(['a ever-growing datasets inside observational astronomy have challenged scientists inside many aspects, including an efficient and interactive data exploration and visualization. many tools have been developed to confront this challenge. however, they usually focus on displaying a actual images or focus on visualizing patterns within catalogs inside the predefined way. inside this paper we introduce vizic, the python visualization library that builds a connection between images and catalogs through an interactive map of a sky region. vizic visualizes catalog data over the custom background canvas with the help of a shape, size and orientation of each object inside a catalog. a displayed objects inside a map are highly interactive and customizable comparing to those inside a images. these objects should be filtered by or colored by their properties, such as redshift and magnitude. they also should be sub-selected with the help of the lasso-like tool considering further analysis w

In [7]:
print("Número de documentos: ",len(corpus))

Número de documentos:  14004


In [8]:
# Preprocesamiento del corpus, se normaliza los documentos:
norm_corpus = utils.normalize_corpus(corpus)

In [12]:
print("Comparación antes vs despues del preprocesamiento: ")
print("Texto antes de ser normalizado:\n")
print(corpus[1][:200]+"\n")
print("Texto después de ser normalizado:\n")
print(norm_corpus[1][:200])


Comparación antes vs despues del preprocesamiento: 
Texto antes de ser normalizado:

we propose the framework considering optimal $t$-matchings excluding a prescribed $t$-factors inside bipartite graphs. a proposed framework was the generalization of a nonbipartite matching problem an

Texto después de ser normalizado:

propose framework considering optimal matchings excluding prescribed factors inside bipartite graph proposed framework wa generalization nonbipartite matching problem includes several problem triangle


In [13]:
# Obtención de la matriz TD-IDF
from sklearn.feature_extraction.text import TfidfVectorizer

tv = TfidfVectorizer(min_df=0., max_df=1., norm='l2',
                     use_idf=True, smooth_idf=True)
tv_matrix = tv.fit_transform(norm_corpus)
tv_matrix = tv_matrix.toarray()

vocab = tv.get_feature_names() # Obtener todas las palabras unicas en el corpus

In [15]:
tv_matrix

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [16]:
vocab

['_a',
 '_b',
 '_c',
 '_catalogue',
 '_cj',
 '_d',
 '_d_',
 '_e',
 '_et',
 '_f',
 '_g',
 '_h',
 '_i',
 '_j',
 '_k',
 '_kink',
 '_l',
 '_lco',
 '_m',
 '_n',
 '_nlco',
 '_p',
 '_q',
 '_r',
 '_s',
 '_su',
 '_t',
 '_u',
 '_v',
 '_w',
 '_x',
 '_x_',
 '_y',
 '_z',
 'a_',
 'a_a_a_a_',
 'a_a_xa_x',
 'a_c',
 'a_d',
 'a_f',
 'a_g',
 'a_h',
 'a_i',
 'a_j',
 'a_k',
 'a_kb_',
 'a_m',
 'a_n',
 'a_nb_',
 'a_r',
 'a_s',
 'a_t_',
 'a_ti',
 'a_u',
 'a_v',
 'a_y',
 'a_yd',
 'aa',
 'aa_',
 'aa_k',
 'aachen',
 'aae',
 'aaes',
 'aalenjohansen',
 'aam',
 'aams',
 'aan',
 'aapm',
 'aaronson',
 'aatwistor',
 'aavso',
 'aaxis',
 'ab',
 'ab_id',
 'abacus',
 'abalone',
 'abandon',
 'abandoned',
 'abandonment',
 'abate',
 'abbe',
 'abboud',
 'abbreviated',
 'abbreviates',
 'abbreviation',
 'abc',
 'abcd',
 'abcmcmc',
 'abcpy',
 'abcrobustlogitboost',
 'abcsl',
 'abcsubsim',
 'abctools',
 'abdmg',
 'abdomen',
 'abdominal',
 'abduction',
 'abe',
 'abel',
 'abelian',
 'abelianhiggs',
 'abelianization',
 'abell',
 'ab

In [30]:
# Matriz TD-IDF
pd.DataFrame(tv_matrix, columns=vocab)

_a   _b   _c  _catalogue  _cj   _d  _d_   _e  _et   _f  ...  zwcl  \
0      0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
1      0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
2      0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
3      0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
4      0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
...    ...  ...  ...         ...  ...  ...  ...  ...  ...  ...  ...   ...   
13999  0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
14000  0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
14001  0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
14002  0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   
14003  0.0  0.0  0.0         0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   0.0   

       zwick  zwicky  zwise  zwitterion  zwittterion  zywina   zz  zz_  zzsun  
0        0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
1        0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
2        0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
3        0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
4        0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
...      ...     ...    ...         ...          ...     ...  ...  ...    ...  
13999    0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
14000    0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
14001    0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
14002    0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  
14003    0.0     0.0    0.0         0.0          0.0     0.0  0.0  0.0    0.0  

[14004 rows x 50661 columns]

In [31]:
from sklearn.metrics.pairwise import cosine_similarity # 2 minutos
similarity_matrix = cosine_similarity(tv_matrix)
similarity_df = pd.DataFrame(similarity_matrix)
similarity_df.head()

0         1         2         3         4         5         6      \
0  1.000000  0.010762  0.029082  0.018119  0.026351  0.030871  0.078171   
1  0.010762  1.000000  0.023854  0.016535  0.013672  0.014149  0.072063   
2  0.029082  0.023854  1.000000  0.069735  0.011783  0.020394  0.047014   
3  0.018119  0.016535  0.069735  1.000000  0.016685  0.008965  0.040152   
4  0.026351  0.013672  0.011783  0.016685  1.000000  0.028597  0.028811   

      7         8         9      ...     13994     13995     13996     13997  \
0  0.041312  0.062039  0.021225  ...  0.042460  0.014581  0.008462  0.008993   
1  0.050292  0.035116  0.010187  ...  0.018148  0.023664  0.024689  0.004338   
2  0.046350  0.014508  0.024247  ...  0.019131  0.091178  0.018350  0.010379   
3  0.046311  0.010489  0.018840  ...  0.020520  0.059116  0.007432  0.027037   
4  0.045849  0.006288  0.004473  ...  0.046190  0.002154  0.017447  0.008267   

      13998     13999     14000     14001     14002     14003  
0  0.031695  0.016148  0.021624  0.018459  0.042962  0.016862  
1  0.061405  0.016113  0.077672  0.017015  0.032609  0.014574  
2  0.038781  0.024295  0.039046  0.079399  0.053393  0.044690  
3  0.011068  0.014251  0.017035  0.125508  0.014151  0.034351  
4  0.026234  0.002870  0.018917  0.012645  0.003036  0.011979  

[5 rows x 14004 columns]

In [58]:
similitudes_doc = similarity_df.iloc[0].values

similar_docs_idxs= np.argsort(-similitudes_doc)[1:11]
similar_docs_idxs

array([13245,  1633,  5351,  5708,   647, 11257,  8150,  5406,  4745,
        1020], dtype=int64)

In [34]:
temas = df[df.columns[2:]]
temas

Computer Science  Mathematics  Physics  Statistics  Analysis of PDEs  \
0                     0            0        1           0                 0   
1                     1            0        0           0                 0   
2                     0            0        1           0                 0   
3                     0            0        1           0                 0   
4                     1            0        0           0                 0   
...                 ...          ...      ...         ...               ...   
13999                 1            0        0           0                 0   
14000                 1            0        0           0                 0   
14001                 0            0        1           0                 0   
14002                 1            0        0           0                 0   
14003                 0            0        1           0                 0   

       Applications  Artificial Intelligence  Astrophysics of Galaxies  \
0                 0                        0                         0   
1                 0                        0                         0   
2                 0                        0                         0   
3                 0                        0                         0   
4                 0                        0                         0   
...             ...                      ...                       ...   
13999             0                        0                         0   
14000             0                        1                         0   
14001             0                        0                         0   
14002             0                        0                         0   
14003             0                        0                         0   

       Computation and Language  Computer Vision and Pattern Recognition  ...  \
0                             0                                        0  ...   
1                             0                                        0  ...   
2                             0                                        0  ...   
3                             0                                        0  ...   
4                             0                                        1  ...   
...                         ...                                      ...  ...   
13999                         0                                        0  ...   
14000                         0                                        1  ...   
14001                         0                                        0  ...   
14002                         1                                        0  ...   
14003                         0                                        0  ...   

       Methodology  Number Theory  Optimization and Control  \
0                0              0                         0   
1                0              0                         0   
2                0              0                         0   
3                0              0                         0   
4                0              0                         0   
...            ...            ...                       ...   
13999            0              0                         0   
14000            0              0                         0   
14001            0              0                         0   
14002            0              0                         0   
14003            0              0                         0   

       Representation Theory  Robotics  Social and Information Networks  \
0                          0         0                                0   
1                          0         0                                0   
2                          0         0                                0   
3                          0         0                                0   
4                          0         0                          

In [59]:
utils.get_topics_of_doc(temas,0)

['Physics',
 'Cosmology and Nongalactic Astrophysics',
 'Instrumentation and Methods for Astrophysics']

In [60]:
utils.num_of_coincidances(similar_docs_idxs,original_paper_idx=0,topics=temas)

7


7

In [51]:
matrix_idx=[]
for similitudes in similarity_df.values:
    print(similitudes)
    similar_docs_idxs= np.argsort(-similitudes)[1:11] # Se excluye el  propio doc
    print(similar_docs_idxs)
    matrix_idx.append(similar_docs_idxs)

[1.         0.0107625  0.02908166 ... 0.01845891 0.04296191 0.01686197]
[13245  1633  5351  5708   647 11257  8150  5406  4745  1020]
[0.0107625  1.         0.02385423 ... 0.01701545 0.03260924 0.01457421]
[10861 10802  5221 10876  5822  1371 12516  6445  2646 11231]
[0.02908166 0.02385423 1.         ... 0.07939928 0.05339315 0.04469012]
[2745 5066  183 7015 6101 6818 8525 9510 3454 5261]
[0.01811869 0.01653466 0.06973537 ... 0.12550786 0.01415068 0.03435096]
[ 2837   641  9789  1281 11608   384  9579  6724  3745 10031]
[0.02635125 0.01367182 0.0117833  ... 0.01264498 0.00303626 0.01197924]
[ 7355  9309  6218  1124  7556  3956  4366 12411  8015 11071]
[0.03087132 0.01414899 0.02039421 ... 0.00657567 0.01911794 0.01372879]
[ 8641    26 11837 11790  7235  9503  1625  5501  8422  8126]
[0.07817114 0.07206268 0.04701433 ... 0.03511002 0.0431441  0.02263596]
[ 6465 11595  7612 10141   587 13845  3006 12157  3189 13062]
[0.04131216 0.05029205 0.04635048 ... 0.0253524  0.02837863 0.03365545]


[12207  9242  2395  5830  2832  9964   587  3912 13977 10134]
[0.01996891 0.13326491 0.02357567 ... 0.00911604 0.01438337 0.00574336]
[10861  1371  8131 11036 12516 10802 11231 11538     1 13673]
[0.03780805 0.0254614  0.0416479  ... 0.00844824 0.04551727 0.0031245 ]
[13174 13186   702  5157 11877  2686  8258  4027  2643  5718]
[0.01399671 0.05122783 0.01885172 ... 0.02785313 0.015565   0.01202321]
[ 4503  3367  5006  4952 10887  3169 13402 13400  1061  3314]
[0.01523372 0.0541248  0.0893566  ... 0.01250919 0.0555881  0.00249423]
[  616  2666  7476  5078  4562 13438 13971  1833  5762  9652]
[0.01863515 0.00695463 0.0164503  ... 0.0263778  0.00883838 0.01233501]
[ 5450   622  1284 13962  1836   370 12630 12113  7349 10636]
[0.02354986 0.01594083 0.05132082 ... 0.02490339 0.006844   0.01321251]
[10787   793  2056 10527  1467  2312  7923 10477  5319  8593]
[0.01894214 0.0481067  0.01424994 ... 0.0153545  0.0208155  0.00904353]
[ 5291  1729  4856  6467 11820 12629 12755 12481  3249 10198]


[ 7146 11255  9254 10019   204  7611  5418 12060  7515  7198]
[0.02015205 0.02386793 0.04194762 ... 0.01204313 0.00416359 0.00903147]
[ 7937 13015 10901  5147 12949  8343 12871  2000    55  4230]
[0.04749725 0.03549516 0.01906502 ... 0.02542029 0.04119042 0.00520381]
[ 2647  5360 10395 10499 13228  5050  4704  4943  6983  9792]
[0.04002618 0.03645849 0.04789425 ... 0.02161886 0.01199545 0.02198763]
[ 5627  2924   101  4146 12699 13212  5709  2904  8576 10663]
[0.01881711 0.0921845  0.03529984 ... 0.01165736 0.05471875 0.00421985]
[ 1783  6383  6359 10658 10464  4736 10861  8474  2460  5114]
[0.04357813 0.034905   0.04478002 ... 0.0363145  0.01207586 0.04496055]
[ 3717  2671  5342  2191  2111    68 12775  3166 13822 11098]
[0.05257644 0.09570363 0.04764135 ... 0.03415744 0.05719175 0.02575827]
[ 5387 10818 11042  3912  2890 13977  8005  7685  8326  3232]
[0.02779009 0.00539176 0.01439378 ... 0.00688811 0.00176944 0.00511231]
[4883 4166 3394 4770 7746 8747 7076 6578 8941 8509]
[0.0328723

[ 8661 12538  9608 12503 10779  9765  6329 13081  2157  7348]
[0.00984791 0.01592802 0.0193186  ... 0.00656081 0.02723557 0.0028909 ]
[ 9097   275  6110 13792  8646  7584  7931 13672  3862  6995]
[0.02720691 0.03048064 0.04307916 ... 0.01720714 0.03045367 0.01593133]
[ 9651   286  2863  5717  7565 13016  6143 13188  5082  3276]
[0.01835752 0.01128285 0.0183331  ... 0.01767328 0.02112572 0.01578211]
[ 3188  7070 11137  9447  5771  8299  9231 13437 13547 13073]
[0.05021282 0.02711733 0.02778938 ... 0.0052166  0.08227171 0.0112885 ]
[ 1116  2082  6096   440 10486 10198  7017  8903 12150  5748]
[0.01889329 0.0430815  0.05848558 ... 0.03110909 0.05870405 0.03579857]
[ 4622 12325  7875  8295  4714  6478 13080 10364 13348  5362]
[0.01745283 0.01802475 0.02535432 ... 0.0183729  0.02136639 0.00805918]
[ 9651  7565  2615 13110  5082  9780 13016  1863  3276   465]
[0.02421959 0.01837311 0.08048231 ... 0.16352058 0.01839607 0.05538034]
[ 6472 12079  8189  4551 13617  1050 12743  7506  6139  2157]


[  151  5450 13962  1836  1284 12113   370 12630  1726  7349]
[0.01162551 0.00960239 0.07052186 ... 0.01320692 0.01728995 0.00466509]
[ 7725  3421  5006 10209  5775  7818  9277  5434  9469  9833]
[0.01659521 0.03922066 0.11789838 ... 0.03883763 0.03464061 0.0221218 ]
[ 4646 11544  5261  1710  1600 13203 11555  9174  7282  4539]
[0.02312405 0.00704659 0.01247954 ... 0.01120684 0.03048369 0.01275502]
[ 1841  3672  3403   559  6383   628 12726 12989  2725  2250]
[0.01257564 0.00455848 0.00241959 ... 0.00416156 0.00059169 0.00151773]
[10446 10734   474  8741  3281  3512  7427  4909  9044 13336]
[0.0310224  0.06055448 0.05475204 ... 0.06193091 0.0411935  0.01436887]
[ 9193 12866  7489  6609 13037  3990  4178  6350  7435  4562]
[0.02280361 0.03926355 0.05668264 ... 0.01986073 0.02727664 0.01194815]
[ 3672  1433 12989 13774  7144  6410  3435  8021 12299 11260]
[0.02535603 0.0075279  0.02983742 ... 0.02201275 0.07726428 0.0180767 ]
[ 2270  8188  7948 10744  8812  9128  4925    51  9339 12784]


...

[ 9464  3277 10189 11350  6438 13465  8335 12807   556  7365]
[0.03662017 0.04529711 0.01884182 ... 0.01932097 0.02621365 0.00335062]
[ 8059 11697  5705  2804  7195  9205  9626  5499 11139  6084]
[0.04607762 0.02613508 0.03278705 ... 0.02505643 0.00803589 0.03203358]
[ 6576  8576 11911  4614  9751  9377  8969  1177  2511  9804]
[0.0042557  0.0019071  0.00466854 ... 0.00392654 0.00185489 0.000638  ]
[  472  7471 10602 13777 11261  1346  5606  5663  4398 10661]
[0.00827451 0.02670748 0.02227558 ... 0.01975355 0.01119927 0.00387388]
[ 4773 11235 10728 13715  2219  8173 11797  9040  7755  6077]
[0.00913595 0.03113678 0.01579726 ... 0.01054164 0.03647644 0.0159691 ]
[12912  1139 10042  9651  3249 13072  9588 10161 10517  2508]
[0.01981703 0.03285211 0.03642586 ... 0.0248431  0.03026758 0.0078756 ]
[ 6166  5271   523  2705  4763 10128 11601  6653  1088  9077]
[0.03222122 0.02058994 0.01929259 ... 0.01361885 0.03044428 0.02297286]
[12552  2303  1671 13731 11550 10804 10223 11766  3324 11718]


[ 1528  9252  9460  2792  4947 11047 13146 10213  2530  1857]
[0.00384715 0.00554746 0.01121802 ... 0.02449452 0.03158513 0.02727794]
[ 7321 11238  7522   425  3944 12043  4818  5257   837  5868]
[0.04580001 0.0314351  0.02612853 ... 0.02144285 0.02564638 0.00804046]
[ 9874   498  1627  3828  8088 13079  5709  7953  4362  6813]
[0.01857008 0.01027164 0.01565406 ... 0.05220253 0.01717039 0.00746405]
[13042  6556  5602  3526 11826 13580  9758  6258 12298  6242]
[0.0367298  0.01707459 0.02807056 ... 0.01947303 0.01245486 0.01261685]
[  588 13000  9199  5585  9043  9157 10717   317    82   767]
[0.04359032 0.01847492 0.02795276 ... 0.01739514 0.09884005 0.02175286]
[ 7672  7592   684  1490  8236 12543   125  2847  3418  7359]
[0.02707034 0.03391697 0.01603857 ... 0.03374564 0.00566493 0.02998474]
[ 3367 10406  4952  5006 10887  3169  5671  1061  7689 13402]
[0.05914632 0.01231432 0.03258801 ... 0.03511588 0.06951579 0.00312166]
[ 1987 12323  2042  5593  4918  7956 10154 10091  4905 11056]


[ 3882  3516 13352  9553  8512  2758  3111  6289 11054  5063]
[0.01091908 0.01813188 0.02394628 ... 0.00992012 0.02303805 0.01615631]
[  322 13960  7631  2297 13849   256  7356  2408 13457  9278]
[0.02258575 0.04930734 0.04178539 ... 0.02011285 0.01152865 0.01576536]
[2714 5362 6271 1668 1241  428 5423 1345 8693 1806]
[0.02804121 0.02740442 0.01442923 ... 0.02017817 0.02402186 0.01462343]
[  834  8414 13566  5939  4017 11150 13539 12111  5694  8891]
[0.00347062 0.0066079  0.02132217 ... 0.00744257 0.00413346 0.00330821]
[ 7481 11027  6868  6030  7518   585 11523  7352  7175  4416]
[0.01107518 0.00793734 0.03142854 ... 0.04377271 0.00389387 0.07199884]
[ 4256 12342 12741  2582  6361  9293 10912  2473  9995  3940]
[0.01037161 0.00599508 0.03794377 ... 0.06425133 0.02304109 0.01606212]
[ 6017 12467 13487  7661 12080  7047  4758  3159 13459 13579]
[0.02352075 0.01777232 0.0204981  ... 0.021136   0.04140503 0.0105554 ]
[12976 10157   289 10782 10013    85  3672  2195 12574  9748]
[0.0073746

[ 8050  8617  6842  3737  1931  6876  8037 11566  6443   660]
[0.02363629 0.07605091 0.01710495 ... 0.03558996 0.03487664 0.00678086]
[11599  4912 10750 10313  8467 11376   628   213  3795  3672]
[0.03917728 0.08971794 0.03020616 ... 0.03011894 0.02685732 0.01437945]
[12701  9415  2887  2659 10797  3746 11548  8997 13092 11112]
[0.04970638 0.0932749  0.06857609 ... 0.0212589  0.01803813 0.01797849]
[  495  1577  3862  9381  7584  2225  3811  8646 11353  9097]
[0.01105708 0.01236253 0.01344924 ... 0.02896921 0.01058384 0.00421695]
[13322   472  7471  8324  3645 10602 11261  1441  5700  9728]
[0.01278891 0.0176802  0.03434163 ... 0.01730997 0.00801115 0.02215266]
[ 8417  4213  4204 12946  1680   623  9539  9353  9033  3421]
[0.00825044 0.         0.         ... 0.         0.         0.0074606 ]
[ 3665  9943 10863  4748    31  9772  9802  2473  6824 13674]
[0.02903577 0.03993887 0.01859356 ... 0.0265001  0.0158286  0.00642075]
[ 1869  5812  4119  5426  4712  2530 13609 13888  5105 13122]


[ 6635  6101  1388 12293   118  9135 13593  2262 12702 12084]
[0.02509971 0.06707709 0.04459558 ... 0.01696716 0.02115458 0.01212618]
[ 4120  6073  4243  7444   447  3483   224 12146  2852 10484]
[0.02432946 0.00794226 0.03942174 ... 0.0276105  0.03237233 0.01760145]
[ 5752  3747  6449  1887  6092  8249  4521  7813 13270 13137]
[0.01297394 0.00660103 0.02492893 ... 0.02442478 0.10737878 0.00339087]
[ 2651  5806   367  7359 11105 11004  9461  8188  2775  3418]
[0.03151934 0.01424141 0.03872535 ... 0.07922356 0.00488921 0.03961814]
[ 5196  4220   273 10733 12662  4867  3952  4690 12029  4488]
[0.03481238 0.03839341 0.05361334 ... 0.01461544 0.04375198 0.0045013 ]
[ 2665  5105   714  3434  1812 12866 13122 12205  7978  4503]
[0.0177965  0.07426026 0.0389315  ... 0.02976738 0.04596248 0.00913938]
[ 2118  2465  2453  7480  3064  3197  8912 12994  1676  5901]
[0.0118817  0.01338225 0.02466731 ... 0.01621627 0.01035084 0.00574657]
[4284 5190 8721 4664 9003 6491 9321 2221 6529 4794]
[0.0173893

In [52]:
# Matriz con los indices de los n documentos más parecidos
matrix_idx = np.array(matrix_idx)


In [53]:
matrix_idx

array([[13245,  1633,  5351, ...,  5406,  4745,  1020],
       [10861, 10802,  5221, ...,  6445,  2646, 11231],
       [ 2745,  5066,   183, ...,  9510,  3454,  5261],
       ...,
       [12017,  6149, 12292, ..., 12413,  3091, 12641],
       [ 8188, 11231,  4954, ...,  7017, 12271,  2670],
       [ 9028, 13031, 12654, ...,  6287,  5219,  4072]], dtype=int64)

In [56]:
i=0
coincidencias=[]
for indices in matrix_idx:
    print(utils.num_of_coincidances(indices,original_paper_idx=i,topics=temas))
    coincidencias.append(utils.num_of_coincidances(indices,original_paper_idx=i,topics=temas))
    i+=1

7
7
7
6
6
6
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
9
9
9
9
9
9
6
6
6
8
8
8
10
10
10
7
7
7
9
9
9
10
10
10
10
10
10
10
10
10
5
5
5
10
10
10
10
10
10
10
10
10
10
10
10
9
9
9
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
7
7
7
10
10
10
7
7
7
7
7
7
5
5
5
8
8
8
10
10
10
3
3
3
5
5
5
6
6
6
9
9
9
10
10
10
8
8
8
10
10
10
10
10
10
7
7
7
10
10
10
9
9
9
10
10
10
6
6
6
10
10
10
7
7
7
10
10
10
10
10
10
9
9
9
3
3
3
7
7
7
10
10
10
4
4
4
8
8
8
7
7
7
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
2
2
2
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
8
8
8
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
8
8
8
10
10
10
9
9
9
7
7
7
8
8
8
4
4
4
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
7
7
7
10
10
10
3
3
3
8
8
8
9
9
9
10
10
10
7
7
7
10
10
10
10
10
10
7
7
7
9
9
9
10
10
10
9
9
9
8
8
8
8
8
8
9
9
9
9
9
9
10
10
10
8
8
8
9
9
9
9
9
9
10
10
10
9
9
9
9
9
9
10
10
10
8
8
8
9
9
9
9
9
9
8
8
8
9
9
9
8
8
8
9
9
9
10
10
10
10
10
10
5
5
5
7
7
7
4
4
4
7
7
7
7
7
7
7
7
7
9
9
9
6
6
6
10
10
10
8
8
8
7
7
7
1

8
8
8
10
10
10
4
4
4
9
9
9
9
9
9
8
8
8
10
10
10
10
10
10
8
8
8
10
10
10
6
6
6
9
9
9
9
9
9
7
7
7
8
8
8
10
10
10
10
10
10
5
5
5
10
10
10
8
8
8
7
7
7
10
10
10
0
0
0
10
10
10
9
9
9
6
6
6
10
10
10
9
9
9
9
9
9
9
9
9
10
10
10
7
7
7
6
6
6
9
9
9
10
10
10
2
2
2
6
6
6
8
8
8
7
7
7
10
10
10
9
9
9
5
5
5
10
10
10
10
10
10
7
7
7
9
9
9
9
9
9
9
9
9
8
8
8
10
10
10
9
9
9
8
8
8
6
6
6
6
6
6
8
8
8
5
5
5
10
10
10
8
8
8
3
3
3
7
7
7
10
10
10
10
10
10
8
8
8
9
9
9
10
10
10
7
7
7
5
5
5
5
5
5
9
9
9
10
10
10
5
5
5
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
3
3
3
10
10
10
6
6
6
10
10
10
10
10
10
8
8
8
5
5
5
10
10
10
9
9
9
10
10
10
9
9
9
5
5
5
8
8
8
9
9
9
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
9
9
9
8
8
8
1
1
1
4
4
4
10
10
10
10
10
10
10
10
10
9
9
9
8
8
8
7
7
7
8
8
8
10
10
10
3
3
3
5
5
5
10
10
10
10
10
10
3
3
3
10
10
10
1
1
1
10
10
10
10
10
10
1
1
1
10
10
10
10
10
10
1
1
1
9
9
9
10
10
10
10
10
10
4
4
4
8
8
8
10
10
10
10
10
10
6
6
6
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
5
5
5
10
10
10
10
1

9
8
8
8
6
6
6
10
10
10
7
7
7
10
10
10
10
10
10
3
3
3
10
10
10
8
8
8
6
6
6
10
10
10
10
10
10
10
10
10
10
10
10
8
8
8
9
9
9
7
7
7
9
9
9
9
9
9
8
8
8
10
10
10
5
5
5
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
6
6
6
5
5
5
9
9
9
10
10
10
8
8
8
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
4
4
4
10
10
10
1
1
1
10
10
10
10
10
10
9
9
9
10
10
10
5
5
5
10
10
10
5
5
5
10
10
10
10
10
10
7
7
7
5
5
5
9
9
9
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
4
4
4
10
10
10
7
7
7
10
10
10
6
6
6
8
8
8
8
8
8
6
6
6
9
9
9
10
10
10
7
7
7
10
10
10
9
9
9
10
10
10
7
7
7
10
10
10
6
6
6
9
9
9
9
9
9
3
3
3
6
6
6
9
9
9
9
9
9
9
9
9
8
8
8
8
8
8
10
10
10
7
7
7
10
10
10
9
9
9
7
7
7
4
4
4
5
5
5
10
10
10
10
10
10
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
9
9
9
8
8
8
8
8
8
10
10
10
10
10
10
6
6
6
9
9
9
10
10
10
6
6
6
9
9
9
5
5
5
10
10
10
7
7
7
10
10
10
9
9
9
10
10
10
4
4
4
10
10
10
8
8
8
4
4
4
10
10
10
10
10
10
7
7
7
4
4
4
10
10
10
8
8
8
8
8
8
8
8
8
6
6
6
10
10
10
10
10
10
8
8
8
10
10
10
8
8
8
7
7
7
9
9
9
4
4
4
8
8
8
9
9
9
9
9
9
7
7
7
10
10
10

10
10
10
10
9
9
9
2
2
2
7
7
7
10
10
10
10
10
10
6
6
6
10
10
10
10
10
10
8
8
8
8
8
8
9
9
9
10
10
10
10
10
10
8
8
8
6
6
6
10
10
10
7
7
7
5
5
5
10
10
10
9
9
9
5
5
5
7
7
7
10
10
10
9
9
9
8
8
8
7
7
7
10
10
10
1
1
1
2
2
2
8
8
8
5
5
5
8
8
8
10
10
10
5
5
5
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
6
6
6
9
9
9
8
8
8
9
9
9
10
10
10
6
6
6
9
9
9
7
7
7
3
3
3
5
5
5
10
10
10
8
8
8
6
6
6
10
10
10
10
10
10
10
10
10
10
10
10
8
8
8
7
7
7
10
10
10
7
7
7
9
9
9
10
10
10
9
9
9
9
9
9
7
7
7
8
8
8
10
10
10
5
5
5
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
0
0
0
9
9
9
8
8
8
9
9
9
7
7
7
10
10
10
10
10
10
7
7
7
10
10
10
7
7
7
4
4
4
10
10
10
10
10
10
6
6
6
10
10
10
8
8
8
10
10
10
7
7
7
9
9
9
10
10
10
10
10
10
10
10
10
7
7
7
9
9
9
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
9
9
9
9
9
9
10
10
10
8
8
8
2
2
2
9
9
9
8
8
8
10
10
10
5
5
5
9
9
9
10
10
10
10
10
10
8
8
8
6
6
6
10
10
10
6
6
6
8
8
8
9
9
9
7
7
7
10
10
10
2
2
2
6
6
6
10
10
10
10
10
10
5
5
5
9
9
9
10
10
10
1

2
10
10
10
1
1
1
10
10
10
10
10
10
10
10
10
6
6
6
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
8
8
8
8
8
8
10
10
10
9
9
9
10
10
10
4
4
4
10
10
10
10
10
10
2
2
2
7
7
7
10
10
10
6
6
6
7
7
7
10
10
10
10
10
10
10
10
10
10
10
10
9
9
9
3
3
3
10
10
10
8
8
8
9
9
9
10
10
10
10
10
10
10
10
10
8
8
8
8
8
8
9
9
9
10
10
10
10
10
10
6
6
6
10
10
10
7
7
7
4
4
4
7
7
7
9
9
9
7
7
7
9
9
9
10
10
10
10
10
10
10
10
10
7
7
7
10
10
10
7
7
7
7
7
7
10
10
10
8
8
8
9
9
9
9
9
9
6
6
6
9
9
9
10
10
10
7
7
7
10
10
10
10
10
10
3
3
3
9
9
9
10
10
10
9
9
9
9
9
9
6
6
6
10
10
10
10
10
10
10
10
10
6
6
6
10
10
10
9
9
9
7
7
7
9
9
9
9
9
9
10
10
10
9
9
9
10
10
10
3
3
3
10
10
10
10
10
10
6
6
6
9
9
9
7
7
7
10
10
10
10
10
10
10
10
10
10
10
10
8
8
8
10
10
10
9
9
9
10
10
10
6
6
6
10
10
10
2
2
2
9
9
9
6
6
6
10
10
10
7
7
7
7
7
7
10
10
10
8
8
8
7
7
7
10
10
10
6
6
6
7
7
7
10
10
10
7
7
7
10
10
10
7
7
7
7
7
7
10
10
10
9
9
9
6
6
6
10
10
10
8
8
8
10
10
10
8
8
8
9
9
9
8
8
8
10
10
10
6
6
6
10
10
10
10
10
10
7
7
7
9
9
9
9
9
9

...

10
10
5
5
5
10
10
10
9
9
9
6
6
6
10
10
10
10
10
10
1
1
1
5
5
5
5
5
5
5
5
5
8
8
8
10
10
10
6
6
6
9
9
9
3
3
3
8
8
8
9
9
9
10
10
10
8
8
8
9
9
9
10
10
10
7
7
7
10
10
10
10
10
10
10
10
10
2
2
2
1
1
1
9
9
9
9
9
9
9
9
9
8
8
8
8
8
8
10
10
10
10
10
10
3
3
3
10
10
10
10
10
10
6
6
6
10
10
10
8
8
8
10
10
10
9
9
9
7
7
7
9
9
9
10
10
10
8
8
8
10
10
10
8
8
8
10
10
10
9
9
9
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
8
8
8
10
10
10
10
10
10
8
8
8
1
1
1
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
8
8
8
9
9
9
4
4
4
8
8
8
10
10
10
9
9
9
10
10
10
6
6
6
10
10
10
10
10
10
9
9
9
10
10
10
9
9
9
10
10
10
8
8
8
7
7
7
8
8
8
10
10
10
4
4
4
10
10
10
10
10
10
7
7
7
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
10
10
10
5
5
5
10
10
10
10
10
10
8
8
8
2
2
2
10
10
10
7
7
7
4
4
4
4
4
4
10
10
10
10
10
10
6
6
6
9
9
9
7
7
7
7
7
7
9
9
9
1
1
1
10
10
10
7
7
7
8
8
8
8
8
8
9
9
9
10
10
10
9
9
9
10
10
10
8
8
8
10
10
10
7
7
7
7
7
7
10
10
10
8
8
8
10
10
10
10
10
10
9
9
9
10
10
10
7
7
7
10
10
10
5
5
5
8
8
8
4
4
4
10
1

10
10
10
10
10
10
4
4
4
10
10
10
9
9
9
9
9
9
8
8
8
6
6
6
9
9
9
7
7
7
10
10
10
10
10
10
5
5
5
10
10
10
10
10
10
9
9
9
10
10
10
5
5
5
10
10
10
10
10
10
10
10
10
9
9
9
6
6
6
10
10
10
9
9
9
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
6
6
6
8
8
8
7
7
7
3
3
3
9
9
9
10
10
10
5
5
5
10
10
10
10
10
10
10
10
10
6
6
6
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
7
7
7
9
9
9
6
6
6
10
10
10
6
6
6
8
8
8
7
7
7
9
9
9
6
6
6
6
6
6
4
4
4
10
10
10
7
7
7
6
6
6
6
6
6
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
5
5
5
10
10
10
7
7
7
9
9
9
8
8
8
10
10
10
9
9
9
10
10
10
10
10
10
4
4
4
8
8
8
10
10
10
10
10
10
10
10
10
8
8
8
3
3
3
3
3
3
9
9
9
8
8
8
10
10
10
8
8
8
9
9
9
4
4
4
9
9
9
8
8
8
10
10
10
10
10
10
10
10
10
7
7
7
10
10
10
8
8
8
9
9
9
10
10
10
10
10
10
5
5
5
10
10
10
9
9
9
4
4
4
9
9
9
8
8
8
3
3
3
10
10
10
9
9
9
10
10
10
5
5
5
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
9
9
9
8
8
8
8
8
8
10
10
10
10
10
10
7
7
7
4
4
4
10
10
10
10
10
10
2
2
2
5
5
5
10
10
10
9

5
5
5
3
3
3
7
7
7
10
10
10
4
4
4
9
9
9
10
10
10
6
6
6
8
8
8
10
10
10
3
3
3
10
10
10
4
4
4
7
7
7
9
9
9
9
9
9
8
8
8
8
8
8
9
9
9
3
3
3
7
7
7
10
10
10
8
8
8
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
9
9
9
9
9
9
8
8
8
6
6
6
9
9
9
6
6
6
7
7
7
9
9
9
4
4
4
8
8
8
10
10
10
10
10
10
10
10
10
7
7
7
10
10
10
4
4
4
10
10
10
10
10
10
9
9
9
5
5
5
10
10
10
7
7
7
8
8
8
9
9
9
8
8
8
10
10
10
10
10
10
10
10
10
8
8
8
9
9
9
10
10
10
8
8
8
10
10
10
9
9
9
7
7
7
7
7
7
9
9
9
10
10
10
10
10
10
6
6
6
10
10
10
7
7
7
9
9
9
8
8
8
10
10
10
4
4
4
10
10
10
8
8
8
10
10
10
10
10
10
1
1
1
10
10
10
10
10
10
10
10
10
8
8
8
7
7
7
5
5
5
5
5
5
8
8
8
9
9
9
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
10
10
10
6
6
6
6
6
6
10
10
10
10
10
10
10
10
10
3
3
3
7
7
7
2
2
2
7
7
7
7
7
7
9
9
9
6
6
6
10
10
10
9
9
9
9
9
9
8
8
8
8
8
8
8
8
8
10
10
10
7
7
7
3
3
3
9
9
9
8
8
8
10
10
10
9
9
9
7
7
7
10
10
10
10
10
10
10
10
10
9
9
9
10
10
10
8
8
8
4
4
4
9
9
9
9
9
9
10
10
10
2
2
2
8
8
8
8
8
8
10
10
10
8
8
8
10
10
10
10
10
10
9
9
9
9
9
9
6
6
6
10
10
10
1

6
6
6
10
10
10
4
4
4
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
5
5
5
4
4
4
8
8
8
9
9
9
9
9
9
7
7
7
9
9
9
10
10
10
10
10
10
9
9
9
9
9
9
5
5
5
1
1
1
6
6
6
10
10
10
8
8
8
10
10
10
8
8
8
10
10
10
8
8
8
8
8
8
9
9
9
8
8
8
9
9
9
10
10
10
10
10
10
8
8
8
6
6
6
9
9
9
7
7
7
8
8
8
9
9
9
10
10
10
0
0
0
9
9
9
7
7
7
5
5
5
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
7
7
7
7
7
7
9
9
9
5
5
5
8
8
8
3
3
3
7
7
7
9
9
9
10
10
10
8
8
8
7
7
7
10
10
10
9
9
9
10
10
10
8
8
8
9
9
9
6
6
6
10
10
10
9
9
9
10
10
10
5
5
5
9
9
9
6
6
6
10
10
10
9
9
9
9
9
9
10
10
10
10
10
10
10
10
10
6
6
6
9
9
9
10
10
10
9
9
9
10
10
10
9
9
9
10
10
10
10
10
10
4
4
4
8
8
8
8
8
8
10
10
10
10
10
10
10
10
10
6
6
6
10
10
10
7
7
7
10
10
10
8
8
8
10
10
10
8
8
8
10
10
10
9
9
9
10
10
10
1
1
1
9
9
9
10
10
10
10
10
10
10
10
10
10
10
10
9
9
9
6
6
6
3
3
3
9
9
9
7
7
7
9
9
9
4
4
4
0
0
0
10
10
10
10
10
10
4
4
4
10
10
10
10
10
10
7
7
7
10
10
10
2
2
2
9
9
9
9
9
9
10
10
10
5
5
5
8
8
8
4
4
4
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
10
10
1

10
10
10
8
8
8
8
8
8
9
9
9
8
8
8
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
6
6
6
8
8
8
5
5
5
9
9
9
10
10
10
8
8
8
7
7
7
9
9
9
5
5
5
8
8
8
10
10
10
10
10
10
7
7
7
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
4
4
4
9
9
9
10
10
10
9
9
9
9
9
9
10
10
10
10
10
10
8
8
8
7
7
7
3
3
3
5
5
5
10
10
10
10
10
10
10
10
10
7
7
7
0
0
0
7
7
7
8
8
8
10
10
10
9
9
9
10
10
10
10
10
10
5
5
5
10
10
10
9
9
9
8
8
8
6
6
6
7
7
7
8
8
8
8
8
8
8
8
8
9
9
9
7
7
7
9
9
9
10
10
10
8
8
8
9
9
9
8
8
8
1
1
1
7
7
7
10
10
10
10
10
10
5
5
5
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
8
8
8
9
9
9
8
8
8
10
10
10
9
9
9
9
9
9
10
10
10
6
6
6
9
9
9
7
7
7
7
7
7
7
7
7
9
9
9
9
9
9
10
10
10
8
8
8
10
10
10
1
1
1
8
8
8
10
10
10
10
10
10
10
10
10
10
10
10
9
9
9
8
8
8
2
2
2
10
10
10
6
6
6
9
9
9
8
8
8
9
9
9
10
10
10
10
10
10
7
7
7
7
7
7
6
6
6
4
4
4
9
9
9
10
10
10
9
9
9
9
9
9
7
7
7
6
6
6
10
10
10
8
8
8
7
7
7
2
2
2
10
10
10
2
2
2
2
2
2
10
10
10
9
9
9
10
10
10
9
9
9
10
10
10
7
7
7
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
1

In [64]:
print(len(coincidencias))
print(sum(coincidencias)/len(coincidencias))
# Este valor indica la exactitud de las s
print(sum(coincidencias)/len(coincidencias)/10)

14004
8.270922593544702
0.8270922593544702


In [ ]:
# Hacer coincidencias de otros rangos

In [65]:
matrix_idx=[]
for similitudes in similarity_df.values:
    print(similitudes)
    similar_docs_idxs= np.argsort(-similitudes)[50:60] # Se excluye el  propio doc
    print(similar_docs_idxs)
    matrix_idx.append(similar_docs_idxs)

[1.         0.0107625  0.02908166 ... 0.01845891 0.04296191 0.01686197]
[ 4179  8760  9288  8088  5643 12230 11486 11663  4822 11547]
[0.0107625  1.         0.02385423 ... 0.01701545 0.03260924 0.01457421]
[ 4299 10010 10763   967   147  8818  6427  4638  1566  3948]
[0.02908166 0.02385423 1.         ... 0.07939928 0.05339315 0.04469012]
[ 3073  8319  7259  7540  5517  6412 12352  8499  7341  3807]
[0.01811869 0.01653466 0.06973537 ... 0.12550786 0.01415068 0.03435096]
[ 4921 11706  3718  8989 12309  6161 11252 13081 14001   531]
[0.02635125 0.01367182 0.0117833  ... 0.01264498 0.00303626 0.01197924]
[12247  1726  5350  8117  8760   356  9530  8472   608  2901]
[0.03087132 0.01414899 0.02039421 ... 0.00657567 0.01911794 0.01372879]
[9144 9154 8136 1583 5168 5065 5874 3295 1802 9835]
[0.07817114 0.07206268 0.04701433 ... 0.03511002 0.0431441  0.02263596]
[ 1360  7361   845 13764 12520  1738 12982 10692 13584  1477]
[0.04131216 0.05029205 0.04635048 ... 0.0253524  0.02837863 0.03365545]


[ 1461 10088 11311 12271  3497  6427 10421  1625  1607  3607]
[0.02776529 0.01340665 0.03348337 ... 0.01422777 0.02871087 0.00592757]
[ 5336 11138  2220 11358 10043   755  7476  9613  3527  4359]
[0.00739407 0.04728564 0.01131634 ... 0.00529159 0.00227496 0.01070869]
[ 5463 13764  3572  9825  1292  9206  8847  8401 13931  2358]
[0.0137429  0.03066985 0.04388189 ... 0.0184067  0.02786558 0.01727841]
[11415  5898  7296 13592  1156  6554  9451  4644 12982   810]
[0.01953363 0.02751357 0.04324859 ... 0.03753086 0.09299026 0.00570088]
[ 1876   386  4348  5663  7351  7491 11353  2857 11488  5740]
[0.00615642 0.00748191 0.00875507 ... 0.00577232 0.00195646 0.0113807 ]
[12938  6411 11678 12337  3410  8753  2729  1338   938  1499]
[0.01132784 0.00827983 0.03344659 ... 0.05429496 0.01049795 0.04878633]
[13081 12292  4339  5098    30  9689   254  9847 11298  2092]
[0.02354141 0.03014439 0.01451706 ... 0.01379689 0.02860413 0.02244666]
[ 2577  3620  7657 13844  4449  8113  8977  8847  4838  1156]


[ 3598 12202  6997 13504  2904  8130  3933  3919  2999   680]
[0.02731376 0.01976022 0.20677138 ... 0.04717498 0.05088004 0.00586684]
[ 6191 10242 13279  7015 10581  2615  2506  8335  2830  2196]
[0.02358653 0.00817005 0.04026814 ... 0.02062185 0.02676695 0.01705288]
[12560  9128 12861   108  7074 10271  8877 10879  1135  6997]
[0.02090875 0.05107013 0.0405153  ... 0.02696095 0.03411179 0.01161512]
[8145 1162  802 6686 9635  697 8551 4543 6644 8752]
[0.0096965  0.02787116 0.02624013 ... 0.02513519 0.001033   0.01761558]
[11298  6938  7322 13073  4206 10163  7954   939  5376  9040]
[0.03116519 0.07215059 0.02613352 ... 0.02241179 0.04778311 0.02700363]
[13781   821  8602  3501  4949  6530 11370  9213   813  7685]
[0.00945463 0.01494883 0.04550235 ... 0.02261971 0.0062817  0.00433449]
[ 3903 11327  8684  9082  6795  2539  1068  6340  8817  8897]
[0.01234385 0.04841836 0.02687684 ... 0.01316281 0.05779677 0.0102583 ]
[6685 5398 6097  113 5270 1883 9500 7181 8721 1759]
[0.01603136 0.030374

[11762   316 10329  4449 10161  5834  7557  4388   697 13633]
[0.00895395 0.01686917 0.04143003 ... 0.00740889 0.00087188 0.0021342 ]
[12091 13417  3682  4562 13728   368  7140 10415   162 13431]
[0.03324507 0.01218931 0.03194373 ... 0.04758789 0.02891162 0.01507361]
[ 9309  8049  3250  2986  5611 10729  5710  9424 11161  7291]
[0.03452829 0.03131884 0.03510018 ... 0.02491579 0.04905902 0.02022438]
[ 2986  9240 11381 11236   484  3693 13166  2326  5596  1023]
[0.01369076 0.02647735 0.01393028 ... 0.01889488 0.00861013 0.06028134]
[10389  1790  5702  7049 10097 13560 12050  7354  6284 10488]
[0.01150308 0.01113464 0.00809837 ... 0.00380111 0.00688507 0.00267295]
[12755  3809  9665 11344  2945 12599   431 13702  3796  7248]
[0.00898409 0.01236416 0.01229605 ... 0.02359155 0.01177325 0.0102012 ]
[ 3672 13204 10731  4239  6832   221  1010   833 13701  4718]
[0.01130957 0.01281695 0.01473023 ... 0.00866889 0.01895972 0.06213585]
[14000  4165  9478  2221 11483  1268  1220  9321   878 12588]


[ 8263  3418  1931 11603 11946 13064  4720 10195  7491  5762]
[0.01376837 0.01128699 0.04514849 ... 0.0156748  0.02381352 0.01586048]
[12570 13817  6116  1237 11458  3242  4708  6095  9390  9895]
[0.01499102 0.03459311 0.00440625 ... 0.0064872  0.00161264 0.0058631 ]
[ 7211  8019  4047 11123 11180 12531 11263  9946 11181  7517]
[0.02538597 0.01594655 0.03343133 ... 0.01853187 0.04876269 0.01843655]
[13783   697 10838 11796 12874 13600 13176 11900  8598 12882]
[0.04560754 0.0111861  0.05284278 ... 0.02084694 0.0071407  0.01145234]
[ 8354  2328 13122  9979 10636  6670 13147  9277  7618  8646]
[0.01790149 0.0194451  0.01663346 ... 0.00989903 0.01407801 0.01666924]
[ 4443 10433  5592 11313  5140  3577  6288 13997  1819  4599]
[0.01454624 0.01955074 0.01856095 ... 0.09046028 0.03323599 0.01008758]
[11946  3449  5565  1095  8706  9039  5800 10993  8611   512]
[0.01313832 0.02752649 0.02221531 ... 0.02624857 0.05381289 0.02310209]
[ 4216  6060   795  8152  5576  3778 13681  6674 10632  1000]


...

[2548 5295 5996  259 1824 5944 8430 8603 6651 2796]
[0.01793405 0.02380523 0.02286592 ... 0.0102481  0.01570336 0.03111981]
[ 8031  3715  8381  1715  2252  5962  1574 12899   197  6382]
[0.01083643 0.00873381 0.03641756 ... 0.026806   0.00284709 0.06439762]
[ 2213  7634 13883  3143 12088 12102  5759 13540  4626  8931]
[0.00576507 0.02628352 0.02572109 ... 0.04437512 0.05637289 0.00740217]
[ 9073  4104 13847 12265  7832 11970  9105  8174 10992  7709]
[0.03347534 0.02273273 0.0397386  ... 0.02180983 0.03186542 0.00796081]
[ 6143  7798 11284 12175  9667  8471    81  9527  1845 12236]
[0.01858358 0.01524904 0.08810686 ... 0.07604294 0.00766842 0.11405478]
[11444  1742  5837  9378  3073  5478  4054 12910  1588  3226]
[0.04664306 0.09840068 0.02347955 ... 0.02048146 0.02838767 0.01234715]
[ 8576  1879 10946  9965  5850 13212 10313 10383  2224  7537]
[0.01306239 0.0117248  0.0415116  ... 0.01994967 0.0106505  0.01798692]
[ 5459   991  5943 10434  8697  3054 12326  4737  6500  3875]
[0.0354601

[ 3666  8539 11263  9238  5720  1625  6962  1091  7573   179]
[0.02997155 0.03772569 0.01354537 ... 0.01221844 0.02977362 0.01025126]
[13789  1888  5708  7079  2546  2675  9855  4254  6199  7320]
[0.00691984 0.02225781 0.08529403 ... 0.02448623 0.01416336 0.03186217]
[ 1458  1736  6124  5004  2369 12547  8328 10598   488  8686]
[0.01738786 0.02239547 0.0129375  ... 0.00269993 0.01447141 0.00280106]
[ 6134 11912  7273  3689  6145  8254  6757  6925  6979 10137]
[0.0129669  0.01207629 0.02445055 ... 0.00568088 0.00767652 0.01091071]
[12771  1253 12412   972 10363  2681 12568  1427 12478  6500]
[0.01727638 0.01707361 0.0325959  ... 0.00831126 0.03437508 0.00415826]
[12272   195  9229  1129  9276  1574   893  9458  7494  6129]
[0.02054349 0.01168791 0.08680706 ... 0.14766853 0.00624051 0.05919943]
[ 5184 11776  6827  8525  8121  3646  5984  1700  9141 13377]
[0.02262018 0.01035401 0.03283105 ... 0.04420089 0.15520015 0.01435663]
[13074  1771 10978 14002 13456 10864  7041  4590  3872 10794]


[ 2554  5369  5521  2801 11638  2136  7848  2110  2869  6417]
[0.02384934 0.02469214 0.02265443 ... 0.01682001 0.05276431 0.00816321]
[ 4822  7375  4413 13325 12111 11774  4120  4485  2925  5638]
[0.00500363 0.00736877 0.04980213 ... 0.08737428 0.0265868  0.00431433]
[ 8207  5995 12293  2213  4672  7787  1503 10048  5739  4153]
[0.02916726 0.01271852 0.01579921 ... 0.01583022 0.02243608 0.00926538]
[ 2006 10894  2572  4641  8997  4780  4442 10327 10797  8359]
[0.02363629 0.07605091 0.01710495 ... 0.03558996 0.03487664 0.00678086]
[ 4725 10736  8111  7740  2530  7938   580  5723  1786  4500]
[0.03917728 0.08971794 0.03020616 ... 0.03011894 0.02685732 0.01437945]
[12334  7009  3175   478   664  3637   738   651  9864  4120]
[0.04970638 0.0932749  0.06857609 ... 0.0212589  0.01803813 0.01797849]
[ 2220  7640  7043  5765  6079 13792  6920  8190 10332 13461]
[0.01105708 0.01236253 0.01344924 ... 0.02896921 0.01058384 0.00421695]
[   78  9757    88 11080 10585  8250  3181 12771  7966 10791]


[ 2247 12960  6719  4175  9027 10429  2530  7851 12596 13888]
[0.03233669 0.01268675 0.0589496  ... 0.05565573 0.08192108 0.00767844]
[ 3856  2460  2458  3985  2104  8047  4927  4165 13290  7319]
[0.00112365 0.04530678 0.00892995 ... 0.01795053 0.0019464  0.03184613]
[ 3072   559  3399  7381  3979  4302  8866 12873  8572   374]
[0.04785319 0.04039926 0.02374612 ... 0.01556913 0.0173541  0.01510944]
[12696  9491  3237  4055  4456  8857  3964  1993 13938  5369]
[0.01452577 0.02058188 0.02735711 ... 0.01663318 0.01790569 0.02999769]
[ 4900   171  7578  6043  7381   655  7515 12530  3308 12056]
[0.01908009 0.08820115 0.03881085 ... 0.01838021 0.03169362 0.00949947]
[ 6891  2904  6427 11918  7515  3347  7438 11690 11035 11055]
[0.02775271 0.01561168 0.04290023 ... 0.01961801 0.0171926  0.01890563]
[  870 13623  8201  4794  4544  8991  2648 13339  2709 12952]
[0.05517428 0.0108127  0.01543976 ... 0.0192788  0.00474908 0.00557148]
[13840  4111 10797 10717  7384  3576  2250  7795  8613  5585]


[ 3968  8453 12109  9833 10400  5932  5295  4672 10940 10808]
[0.02509971 0.06707709 0.04459558 ... 0.01696716 0.02115458 0.01212618]
[12181  1028 10638   760 12592  4573  7409  4615  8471 12870]
[0.02432946 0.00794226 0.03942174 ... 0.0276105  0.03237233 0.01760145]
[10955  7597  8657  8286  8928  7963 10199  6636  5804 11869]
[0.01297394 0.00660103 0.02492893 ... 0.02442478 0.10737878 0.00339087]
[ 6872  6929  3013 11853  3369 10314  5620 13504  6885 13488]
[0.03151934 0.01424141 0.03872535 ... 0.07922356 0.00488921 0.03961814]
[ 3454 12089  3709 10609  8580  3748  7204  6434  6294  2743]
[0.03481238 0.03839341 0.05361334 ... 0.01461544 0.04375198 0.0045013 ]
[12222 10884  4612  3943   682  7663  7941   511  1382 11504]
[0.0177965  0.07426026 0.0389315  ... 0.02976738 0.04596248 0.00913938]
[ 6466  2703  6946 11113  9077 12009  7068  2304  3862 12139]
[0.0118817  0.01338225 0.02466731 ... 0.01621627 0.01035084 0.00574657]
[ 7582 12110  1220  3458  6312 10759  1535  9783 12588  8156]


In [67]:
matrix_idx = np.array(matrix_idx)

In [68]:
i=0
coincidencias=[]
for indices in matrix_idx:
    print(utils.num_of_coincidances(indices,original_paper_idx=i,topics=temas))
    coincidencias.append(utils.num_of_coincidances(indices,original_paper_idx=i,topics=temas))
    i+=1

3
3
3
8
8
8
7
7
7
9
9
9
10
10
10
4
4
4
7
7
7
10
10
10
9
9
9
6
6
6
7
7
7
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
8
8
8
5
5
5
9
9
9
9
9
9
8
8
8
9
9
9
6
6
6
10
10
10
10
10
10
9
9
9
8
8
8
10
10
10
10
10
10
7
7
7
10
10
10
4
4
4
10
10
10
8
8
8
6
6
6
6
6
6
5
5
5
10
10
10
6
6
6
8
8
8
5
5
5
7
7
7
10
10
10
7
7
7
9
9
9
8
8
8
8
8
8
7
7
7
8
8
8
9
9
9
8
8
8
10
10
10
5
5
5
9
9
9
9
9
9
7
7
7
6
6
6
10
10
10
5
5
5
4
4
4
6
6
6
8
8
8
9
9
9
9
9
9
10
10
10
8
8
8
9
9
9
1
1
1
9
9
9
10
10
10
9
9
9
9
9
9
8
8
8
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
6
6
6
5
5
5
10
10
10
10
10
10
10
10
10
7
7
7
7
7
7
6
6
6
9
9
9
10
10
10
8
8
8
7
7
7
10
10
10
10
10
10
9
9
9
9
9
9
5
5
5
10
10
10
3
3
3
7
7
7
8
8
8
9
9
9
7
7
7
10
10
10
9
9
9
4
4
4
10
10
10
8
8
8
10
10
10
8
8
8
10
10
10
7
7
7
9
9
9
10
10
10
4
4
4
10
10
10
9
9
9
10
10
10
10
10
10
4
4
4
10
10
10
5
5
5
10
10
10
4
4
4
7
7
7
4
4
4
7
7
7
9
9
9
8
8
8
10
10
10
6
6
6
6
6
6
2
2
2
5
5
5
5
5
5
6
6
6
6
6
6
8
8
8
9
9
9
8
8
8
7
7
7
9
9
9
9
9
9
5
5
5
8
8
8
8
8
8
10
10
10
10
10
10
1

9
10
10
10
8
8
8
4
4
4
6
6
6
5
5
5
4
4
4
4
4
4
8
8
8
10
10
10
5
5
5
10
10
10
9
9
9
6
6
6
10
10
10
9
9
9
3
3
3
8
8
8
7
7
7
10
10
10
7
7
7
8
8
8
9
9
9
9
9
9
10
10
10
10
10
10
7
7
7
5
5
5
6
6
6
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
10
10
10
8
8
8
1
1
1
6
6
6
9
9
9
7
7
7
8
8
8
9
9
9
8
8
8
6
6
6
9
9
9
10
10
10
0
0
0
4
4
4
10
10
10
10
10
10
9
9
9
10
10
10
3
3
3
7
7
7
10
10
10
1
1
1
10
10
10
8
8
8
1
1
1
9
9
9
10
10
10
9
9
9
6
6
6
6
6
6
10
10
10
10
10
10
7
7
7
10
10
10
7
7
7
8
8
8
10
10
10
10
10
10
10
10
10
8
8
8
10
10
10
8
8
8
3
3
3
9
9
9
9
9
9
9
9
9
6
6
6
9
9
9
5
5
5
10
10
10
10
10
10
9
9
9
6
6
6
10
10
10
8
8
8
8
8
8
7
7
7
8
8
8
8
8
8
6
6
6
4
4
4
8
8
8
9
9
9
4
4
4
10
10
10
5
5
5
10
10
10
9
9
9
8
8
8
7
7
7
8
8
8
10
10
10
10
10
10
5
5
5
7
7
7
10
10
10
7
7
7
10
10
10
10
10
10
7
7
7
9
9
9
9
9
9
10
10
10
10
10
10
6
6
6
4
4
4
5
5
5
9
9
9
8
8
8
7
7
7
9
9
9
6
6
6
8
8
8
8
8
8
4
4
4
10
10
10
0
0
0
4
4
4
8
8
8
8
8
8
3
3
3
9
9
9
9
9
9
2
2
2
10
10
10
2
2
2
6
6
6
5
5
5
9
9
9
10
10
10
10
10

9
9
9
9
10
10
10
8
8
8
4
4
4
10
10
10
10
10
10
4
4
4
10
10
10
8
8
8
7
7
7
7
7
7
6
6
6
2
2
2
9
9
9
9
9
9
5
5
5
9
9
9
10
10
10
6
6
6
3
3
3
10
10
10
8
8
8
9
9
9
5
5
5
4
4
4
7
7
7
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
7
7
7
10
10
10
7
7
7
9
9
9
9
9
9
7
7
7
10
10
10
6
6
6
6
6
6
8
8
8
7
7
7
8
8
8
9
9
9
6
6
6
9
9
9
7
7
7
8
8
8
4
4
4
10
10
10
5
5
5
9
9
9
10
10
10
2
2
2
6
6
6
2
2
2
10
10
10
5
5
5
4
4
4
8
8
8
9
9
9
10
10
10
9
9
9
10
10
10
7
7
7
8
8
8
8
8
8
6
6
6
7
7
7
9
9
9
8
8
8
9
9
9
9
9
9
7
7
7
8
8
8
6
6
6
6
6
6
10
10
10
7
7
7
10
10
10
9
9
9
9
9
9
8
8
8
10
10
10
7
7
7
9
9
9
6
6
6
8
8
8
8
8
8
8
8
8
3
3
3
3
3
3
10
10
10
9
9
9
9
9
9
6
6
6
10
10
10
6
6
6
10
10
10
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
10
10
10
3
3
3
6
6
6
9
9
9
10
10
10
5
5
5
7
7
7
8
8
8
9
9
9
5
5
5
7
7
7
10
10
10
7
7
7
10
10
10
10
10
10
9
9
9
9
9
9
10
10
10
8
8
8
9
9
9
10
10
10
10
10
10
9
9
9
8
8
8
10
10
10
9
9
9
6
6
6
10
10
10
9
9
9
5
5
5
8
8
8
3
3
3
4
4
4
9
9
9
9
9
9
6
6
6
10
10
10
10
10
10
9
9
9
10
10
10
7
7
7
8
8
8
9
9
9

9
7
7
7
4
4
4
5
5
5
9
9
9
6
6
6
10
10
10
9
9
9
8
8
8
10
10
10
8
8
8
2
2
2
9
9
9
10
10
10
7
7
7
7
7
7
6
6
6
3
3
3
6
6
6
10
10
10
8
8
8
5
5
5
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
3
3
3
9
9
9
9
9
9
10
10
10
6
6
6
6
6
6
8
8
8
8
8
8
10
10
10
8
8
8
8
8
8
9
9
9
7
7
7
9
9
9
10
10
10
8
8
8
5
5
5
4
4
4
4
4
4
9
9
9
9
9
9
6
6
6
10
10
10
8
8
8
9
9
9
10
10
10
7
7
7
6
6
6
8
8
8
7
7
7
7
7
7
10
10
10
9
9
9
9
9
9
5
5
5
9
9
9
4
4
4
6
6
6
10
10
10
10
10
10
8
8
8
9
9
9
8
8
8
7
7
7
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
7
7
7
10
10
10
9
9
9
10
10
10
2
2
2
10
10
10
9
9
9
5
5
5
6
6
6
5
5
5
10
10
10
9
9
9
10
10
10
10
10
10
6
6
6
6
6
6
9
9
9
10
10
10
6
6
6
9
9
9
10
10
10
6
6
6
10
10
10
6
6
6
7
7
7
10
10
10
10
10
10
9
9
9
4
4
4
9
9
9
3
3
3
7
7
7
9
9
9
7
7
7
9
9
9
7
7
7
4
4
4
10
10
10
10
10
10
5
5
5
7
7
7
10
10
10
4
4
4
10
10
10
10
10
10
7
7
7
7
7
7
7
7
7
8
8
8
8
8
8
10
10
10
5
5
5
5
5
5
9
9
9
10
10
10
9
9
9
6
6
6
7
7
7
10
10
10
9
9
9
7
7
7
7


3
6
6
6
8
8
8
8
8
8
8
8
8
10
10
10
10
10
10
6
6
6
8
8
8
10
10
10
7
7
7
10
10
10
7
7
7
3
3
3
10
10
10
8
8
8
6
6
6
9
9
9
5
5
5
6
6
6
10
10
10
7
7
7
10
10
10
5
5
5
8
8
8
9
9
9
8
8
8
10
10
10
10
10
10
10
10
10
9
9
9
5
5
5
3
3
3
10
10
10
7
7
7
5
5
5
9
9
9
7
7
7
7
7
7
8
8
8
8
8
8
7
7
7
9
9
9
8
8
8
4
4
4
10
10
10
9
9
9
5
5
5
10
10
10
9
9
9
8
8
8
10
10
10
10
10
10
5
5
5
10
10
10
9
9
9
9
9
9
8
8
8
8
8
8
9
9
9
8
8
8
8
8
8
8
8
8
6
6
6
10
10
10
10
10
10
8
8
8
10
10
10
10
10
10
10
10
10
6
6
6
10
10
10
1
1
1
1
1
1
3
3
3
8
8
8
9
9
9
8
8
8
8
8
8
1
1
1
4
4
4
9
9
9
10
10
10
4
4
4
7
7
7
8
8
8
9
9
9
10
10
10
8
8
8
10
10
10
9
9
9
5
5
5
9
9
9
10
10
10
8
8
8
8
8
8
7
7
7
10
10
10
4
4
4
10
10
10
6
6
6
2
2
2
8
8
8
3
3
3
9
9
9
7
7
7
7
7
7
10
10
10
6
6
6
8
8
8
5
5
5
6
6
6
6
6
6
8
8
8
6
6
6
9
9
9
10
10
10
9
9
9
9
9
9
7
7
7
8
8
8
7
7
7
9
9
9
7
7
7
4
4
4
8
8
8
8
8
8
7
7
7
10
10
10
9
9
9
8
8
8
8
8
8
7
7
7
10
10
10
10
10
10
9
9
9
9
9
9
9
9
9
5
5
5
9
9
9
5
5
5
10
10
10
6
6
6
4
4
4
3
3
3
10
10
10
8
8
8
10
10
10
4
4
4
10

...

9
10
10
10
4
4
4
5
5
5
10
10
10
10
10
10
10
10
10
9
9
9
9
9
9
8
8
8
7
7
7
5
5
5
9
9
9
8
8
8
7
7
7
10
10
10
1
1
1
10
10
10
10
10
10
9
9
9
10
10
10
8
8
8
10
10
10
10
10
10
7
7
7
8
8
8
9
9
9
10
10
10
9
9
9
9
9
9
5
5
5
7
7
7
9
9
9
10
10
10
6
6
6
10
10
10
4
4
4
7
7
7
9
9
9
10
10
10
4
4
4
3
3
3
1
1
1
9
9
9
8
8
8
9
9
9
3
3
3
10
10
10
8
8
8
10
10
10
6
6
6
5
5
5
4
4
4
5
5
5
7
7
7
9
9
9
2
2
2
0
0
0
7
7
7
10
10
10
10
10
10
7
7
7
6
6
6
10
10
10
9
9
9
8
8
8
7
7
7
5
5
5
5
5
5
8
8
8
5
5
5
5
5
5
8
8
8
2
2
2
7
7
7
10
10
10
10
10
10
9
9
9
9
9
9
8
8
8
9
9
9
5
5
5
4
4
4
8
8
8
6
6
6
6
6
6
10
10
10
8
8
8
10
10
10
7
7
7
10
10
10
10
10
10
1
1
1
8
8
8
2
2
2
10
10
10
10
10
10
5
5
5
4
4
4
10
10
10
5
5
5
8
8
8
10
10
10
9
9
9
6
6
6
10
10
10
10
10
10
10
10
10
7
7
7
7
7
7
7
7
7
5
5
5
8
8
8
10
10
10
7
7
7
9
9
9
6
6
6
9
9
9
10
10
10
10
10
10
6
6
6
9
9
9
8
8
8
7
7
7
10
10
10
7
7
7
4
4
4
7
7
7
7
7
7
3
3
3
8
8
8
8
8
8
9
9
9
9
9
9
3
3
3
8
8
8
8
8
8
9
9
9
10
10
10
9
9
9
8
8
8
4
4
4
7
7
7
3
3
3
9
9
9
7
7
7
6
6
6
0
0
0
10
10

5
9
9
9
9
9
9
6
6
6
10
10
10
9
9
9
10
10
10
9
9
9
10
10
10
3
3
3
8
8
8
8
8
8
10
10
10
10
10
10
7
7
7
8
8
8
8
8
8
5
5
5
7
7
7
7
7
7
4
4
4
6
6
6
10
10
10
3
3
3
8
8
8
10
10
10
7
7
7
10
10
10
5
5
5
10
10
10
9
9
9
3
3
3
9
9
9
9
9
9
10
10
10
8
8
8
10
10
10
9
9
9
9
9
9
3
3
3
4
4
4
10
10
10
10
10
10
9
9
9
10
10
10
10
10
10
4
4
4
9
9
9
10
10
10
6
6
6
7
7
7
9
9
9
10
10
10
9
9
9
9
9
9
5
5
5
10
10
10
10
10
10
9
9
9
6
6
6
10
10
10
10
10
10
8
8
8
8
8
8
10
10
10
9
9
9
4
4
4
1
1
1
4
4
4
10
10
10
7
7
7
6
6
6
9
9
9
10
10
10
10
10
10
6
6
6
10
10
10
2
2
2
7
7
7
10
10
10
9
9
9
6
6
6
9
9
9
8
8
8
8
8
8
6
6
6
9
9
9
10
10
10
10
10
10
7
7
7
8
8
8
9
9
9
10
10
10
9
9
9
7
7
7
7
7
7
10
10
10
4
4
4
10
10
10
10
10
10
10
10
10
4
4
4
7
7
7
10
10
10
7
7
7
7
7
7
2
2
2
8
8
8
8
8
8
3
3
3
8
8
8
3
3
3
9
9
9
9
9
9
9
9
9
9
9
9
8
8
8
9
9
9
10
10
10
7
7
7
10
10
10
10
10
10
5
5
5
3
3
3
6
6
6
6
6
6
8
8
8
7
7
7
10
10
10
3
3
3
9
9
9
5
5
5
8
8
8
10
10
10
9
9
9
3
3
3
6
6
6
9
9
9
10
10
10
9
9
9
10
10
10
9
9
9
4
4
4
10
10
10
8
8
8
8
8
8

10
10
10
3
3
3
6
6
6
4
4
4
6
6
6
10
10
10
6
6
6
9
9
9
9
9
9
6
6
6
8
8
8
9
9
9
9
9
9
10
10
10
4
4
4
8
8
8
9
9
9
10
10
10
8
8
8
9
9
9
10
10
10
5
5
5
10
10
10
4
4
4
8
8
8
0
0
0
10
10
10
9
9
9
8
8
8
9
9
9
5
5
5
6
6
6
4
4
4
10
10
10
7
7
7
6
6
6
7
7
7
7
7
7
5
5
5
9
9
9
10
10
10
10
10
10
8
8
8
7
7
7
7
7
7
7
7
7
8
8
8
4
4
4
8
8
8
10
10
10
7
7
7
2
2
2
5
5
5
4
4
4
6
6
6
7
7
7
10
10
10
10
10
10
7
7
7
6
6
6
9
9
9
9
9
9
10
10
10
5
5
5
9
9
9
9
9
9
10
10
10
7
7
7
6
6
6
10
10
10
2
2
2
2
2
2
9
9
9
8
8
8
6
6
6
9
9
9
5
5
5
8
8
8
7
7
7
10
10
10
10
10
10
8
8
8
7
7
7
10
10
10
10
10
10
10
10
10
6
6
6
10
10
10
8
8
8
10
10
10
9
9
9
8
8
8
9
9
9
10
10
10
4
4
4
10
10
10
3
3
3
5
5
5
4
4
4
7
7
7
10
10
10
2
2
2
9
9
9
10
10
10
7
7
7
10
10
10
10
10
10
6
6
6
8
8
8
6
6
6
6
6
6
8
8
8
4
4
4
8
8
8
4
4
4
0
0
0
8
8
8
9
9
9
9
9
9
10
10
10
10
10
10
6
6
6
10
10
10
6
6
6
9
9
9
8
8
8
10
10
10
10
10
10
8
8
8
10
10
10
9
9
9
9
9
9
5
5
5
9
9
9
10
10
10
10
10
10
9
9
9
10
10
10
7
7
7
10
10
10
10
10
10
8
8
8
7
7
7
9
9
9
9
9
9
10
10
10
0

6
6
6
10
10
10
9
9
9
6
6
6
9
9
9
9
9
9
6
6
6
4
4
4
7
7
7
9
9
9
6
6
6
5
5
5
10
10
10
6
6
6
9
9
9
9
9
9
9
9
9
6
6
6
9
9
9
10
10
10
9
9
9
9
9
9
10
10
10
1
1
1
10
10
10
10
10
10
10
10
10
9
9
9
7
7
7
9
9
9
8
8
8
8
8
8
10
10
10
4
4
4
10
10
10
7
7
7
8
8
8
10
10
10
6
6
6
7
7
7
10
10
10
6
6
6
9
9
9
10
10
10
9
9
9
8
8
8
8
8
8
7
7
7
9
9
9
9
9
9
10
10
10
3
3
3
9
9
9
8
8
8
10
10
10
8
8
8
10
10
10
10
10
10
7
7
7
10
10
10
7
7
7
7
7
7
5
5
5
10
10
10
6
6
6
9
9
9
3
3
3
8
8
8
10
10
10
10
10
10
4
4
4
6
6
6
7
7
7
8
8
8
2
2
2
6
6
6
4
4
4
9
9
9
7
7
7
8
8
8
3
3
3
8
8
8
10
10
10
3
3
3
8
8
8
5
5
5
8
8
8
8
8
8
10
10
10
6
6
6
10
10
10
7
7
7
10
10
10
3
3
3
4
4
4
9
9
9
9
9
9
7
7
7
10
10
10
8
8
8
8
8
8
4
4
4
9
9
9
5
5
5
6
6
6
8
8
8
8
8
8
8
8
8
9
9
9
7
7
7
5
5
5
6
6
6
8
8
8
9
9
9
7
7
7
8
8
8
7
7
7
10
10
10
7
7
7
10
10
10
9
9
9
6
6
6
8
8
8
10
10
10
10
10
10
10
10
10
10
10
10
9
9
9
10
10
10
9
9
9
5
5
5
9
9
9
9
9
9
10
10
10
9
9
9
2
2
2
10
10
10
10
10
10
8
8
8
10
10
10
8
8
8
5
5
5
10
10
10
7
7
7
8
8
8
7
7
7
10
10
10
7
7


3
10
10
10
3
3
3
10
10
10
7
7
7
9
9
9
9
9
9
9
9
9
10
10
10
9
9
9
10
10
10
10
10
10
8
8
8
8
8
8
8
8
8
6
6
6
7
7
7
10
10
10
6
6
6
5
5
5
8
8
8
9
9
9
7
7
7
8
8
8
8
8
8
5
5
5
8
8
8
8
8
8
6
6
6
9
9
9
7
7
7
4
4
4
3
3
3
9
9
9
10
10
10
9
9
9
9
9
9
7
7
7
7
7
7
9
9
9
8
8
8
9
9
9
9
9
9
8
8
8
8
8
8
8
8
8
5
5
5
10
10
10
10
10
10
10
10
10
10
10
10
4
4
4
6
6
6
10
10
10
9
9
9
10
10
10
9
9
9
9
9
9
10
10
10
1
1
1
9
9
9
10
10
10
10
10
10
10
10
10
5
5
5
7
7
7
9
9
9
6
6
6
9
9
9
8
8
8
8
8
8
9
9
9
5
5
5
10
10
10
9
9
9
9
9
9
6
6
6
3
3
3
6
6
6
8
8
8
8
8
8
9
9
9
3
3
3
6
6
6
10
10
10
4
4
4
4
4
4
10
10
10
10
10
10
2
2
2
6
6
6
5
5
5
9
9
9
6
6
6
9
9
9
9
9
9
10
10
10
9
9
9
10
10
10
5
5
5
9
9
9
3
3
3
6
6
6
8
8
8
3
3
3
10
10
10
2
2
2
9
9
9
6
6
6
7
7
7
7
7
7
3
3
3
5
5
5
10
10
10
10
10
10
8
8
8
8
8
8
10
10
10
9
9
9
8
8
8
10
10
10
10
10
10
8
8
8
7
7
7
7
7
7
7
7
7
5
5
5
4
4
4
10
10
10
8
8
8
7
7
7
10
10
10
10
10
10
6
6
6
8
8
8
2
2
2
9
9
9
7
7
7
10
10
10
10
10
10
7
7
7
6
6
6
7
7
7
10
10
10
3
3
3
6
6
6
6
6
6
9
9
9
8
8
8
8
8
8

In [ ]:
print(len(coincidencias))
print(sum(coincidencias)/len(coincidencias))
# Este valor indica la exactitud de las s
print(sum(coincidencias)/len(coincidencias)/10)w